In [709]:
import glob
import matplotlib.pyplot as plt
import pandas as pd
from PIL import Image
import json
import numpy as np
import scipy.stats
from loaddata import *
import collections
from mapping import *
import tqdm
from loaddata import *
from results import *
from visualize import *
from itertools import zip_longest

%matplotlib inline
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [2]:
class_map = ClassMapping()

In [682]:
class PMF(collections.Counter):
    """A Counter with probabilities."""

    def normalize(self):
        """Normalizes the PMF so the probabilities add to 1."""
        total = float(sum(self.values()))
        for key in self:
            self[key] /= total

    def __hash__(self):
        """Returns an integer hash value."""
        return id(self)

    def __eq__(self, other):
        return self is other

    def __mul__(self, val):
        pmf = PMF()
        if isinstance(val, float):
            for key in self:
                pmf[key] = self[key] * val
        return pmf
    
    def __rmul__(self, val):
        return self.__mul__(val)
    
    def argleq(self, p):
        vals = []
        for k, v in self.items():
            if v <= p:
                vals.append(k)
        return vals

    def render(self):
        """Returns values and their probabilities, suitable for plotting."""
        return zip(*sorted(self.items()))


In [684]:
pmf = PMF()
pmf["a"] += 1
pmf *= 0.1
print(b, pmf)

PMF({'a': 0.1}) PMF({'a': 0.1})


In [3]:
merged = load_merged()

In [753]:
image_priors = loadmergedresults(["20210528prior_3"])

Dir 20210528prior_3
Read  20210528prior_3/topk_ids1622244297.145154.csv 25985
Read  20210528prior_3/topk_ids1622243490.991741.csv 25985
Read  20210528prior_3/topk_ids1622245103.709827.csv 25985
Mode
Total  25985


In [755]:
image_priors["image_id"] = image_priors["filename"].str[:-4]

In [756]:
image_priors.head()

filename  net_id  confidence  \
0  8a0a5ea2-21bc-11ea-a13a-137349068a90.jpg       2    0.258927   
1  8a0a30c6-21bc-11ea-a13a-137349068a90.jpg      24    0.482324   
2  8a0a92a0-21bc-11ea-a13a-137349068a90.jpg     194    0.671640   
3  8a0a4156-21bc-11ea-a13a-137349068a90.jpg     162    0.369837   
4  8a0a8558-21bc-11ea-a13a-137349068a90.jpg      15    0.855437   

                               image_id  idx  
0  8a0a5ea2-21bc-11ea-a13a-137349068a90  NaN  
1  8a0a30c6-21bc-11ea-a13a-137349068a90  NaN  
2  8a0a92a0-21bc-11ea-a13a-137349068a90  NaN  
3  8a0a4156-21bc-11ea-a13a-137349068a90  NaN  
4  8a0a8558-21bc-11ea-a13a-137349068a90  NaN

In [433]:
def get_class_distribution(df):
    c = collections.Counter(df["net_id"])
    return c

merged["net_id"] = merged["category_id"].apply(class_map.reverse)
prior = get_class_distribution(merged)

20910

In [439]:
total = sum(prior.values(), 0.0)
for key in prior:
    prior[key] /= total

In [157]:
sub_tmp = pd.read_csv("sample_submission.csv")
col_Predicted = [col for col in sub_tmp.columns if "Predicted" in col]

In [158]:
sub_tmp.head()

Id  Predicted2  Predicted3  Predicted4  \
0  32ce8026-7ec9-11eb-b675-4f3cc0c82eb3           4           2           8   
1  945c6602-21bc-11ea-a13a-137349068a90           2           5           5   
2  a91c7e26-0cd3-11eb-bed1-0242ac1c0002           0           0           3   
3  9926239e-21bc-11ea-a13a-137349068a90           6           9           4   
4  9672184c-21bc-11ea-a13a-137349068a90           4           1           5   

   Predicted6  Predicted7  Predicted8  Predicted9  Predicted10  Predicted12  \
0           3           6           6           6            3            6   
1           8           5           4           2            3            1   
2           5           8           3           5            4            6   
3           5           1           5           3            1            9   
4           8           8           4           1            7            1   

   ...  Predicted559  Predicted562  Predicted563  Predicted564  Predicted565  \
0  ...             6             4             1             0             9   
1  ...             0             8             4             3             9   
2  ...             2             3             9             6             3   
3  ...             6             0             5             1             9   
4  ...             2             4             3             2             0   

   Predicted566  Predicted567  Predicted568  Predicted570  Predicted571  
0             5             5             1             5             8  
1             1             6             7             2             4  
2             7             9             2             6             5  
3             0             4             9             7             7  
4             6             5             3             9             3  

[5 rows x 205 columns]

In [6]:
sub_tmp.sum()

Id              32ce8026-7ec9-11eb-b675-4f3cc0c82eb3945c6602-2...
Predicted2                                                  49741
Predicted3                                                  49739
Predicted4                                                  49647
Predicted6                                                  49096
                                      ...                        
Predicted566                                                49810
Predicted567                                                49595
Predicted568                                                49721
Predicted570                                                50399
Predicted571                                                50257
Length: 205, dtype: object

In [7]:
df_test_info_gps = load_testinfo_gps()
df_test_info_gps.head()

Loading formatted geocoded file...


height                              image_id  \
0    1024  8b31d3be-21bc-11ea-a13a-137349068a90   
1    1024  8cf202be-21bc-11ea-a13a-137349068a90   
2    1024  8a87e62e-21bc-11ea-a13a-137349068a90   
3    1024  8e6994f4-21bc-11ea-a13a-137349068a90   
4    1024  948b29e2-21bc-11ea-a13a-137349068a90   

                                 seq_id  location  width  \
0  a91ebc18-0cd3-11eb-bed1-0242ac1c0002        20   1280   
1  a91ebc18-0cd3-11eb-bed1-0242ac1c0002        20   1280   
2  a91ebc18-0cd3-11eb-bed1-0242ac1c0002        20   1280   
3  a91ebc18-0cd3-11eb-bed1-0242ac1c0002        20   1280   
4  a91ebc18-0cd3-11eb-bed1-0242ac1c0002        20   1280   

                  datetime                                 file_name  \
0  2013-06-09 16:01:38.000  8b31d3be-21bc-11ea-a13a-137349068a90.jpg   
1  2013-06-09 16:01:39.000  8cf202be-21bc-11ea-a13a-137349068a90.jpg   
2  2013-06-09 16:01:40.000  8a87e62e-21bc-11ea-a13a-137349068a90.jpg   
3  2013-06-09 16:01:41.000  8e6994f4-21bc-11ea-a13a-137349068a90.jpg   
4  2013-06-09 16:01:42.000  948b29e2-21bc-11ea-a13a-137349068a90.jpg   

   seq_frame_num  seq_num_frames  sub_location  CC  
0              0              10           NaN  BZ  
1              1              10           NaN  BZ  
2              2              10           NaN  BZ  
3              3              10           NaN  BZ  
4              4              10           NaN  BZ

In [534]:
df = load_olddata("20210409")
old_results = pd.merge(df_test_info_gps, df, on="image_id", how="left")

In [541]:
old_results["category_id"] = old_results["net_id"].apply(class_map)
old_results.head()

height                              image_id  \
0    1024  8b31d3be-21bc-11ea-a13a-137349068a90   
1    1024  8cf202be-21bc-11ea-a13a-137349068a90   
2    1024  8a87e62e-21bc-11ea-a13a-137349068a90   
3    1024  8e6994f4-21bc-11ea-a13a-137349068a90   
4    1024  948b29e2-21bc-11ea-a13a-137349068a90   

                                 seq_id  location  width  \
0  a91ebc18-0cd3-11eb-bed1-0242ac1c0002        20   1280   
1  a91ebc18-0cd3-11eb-bed1-0242ac1c0002        20   1280   
2  a91ebc18-0cd3-11eb-bed1-0242ac1c0002        20   1280   
3  a91ebc18-0cd3-11eb-bed1-0242ac1c0002        20   1280   
4  a91ebc18-0cd3-11eb-bed1-0242ac1c0002        20   1280   

                  datetime                                 file_name  \
0  2013-06-09 16:01:38.000  8b31d3be-21bc-11ea-a13a-137349068a90.jpg   
1  2013-06-09 16:01:39.000  8cf202be-21bc-11ea-a13a-137349068a90.jpg   
2  2013-06-09 16:01:40.000  8a87e62e-21bc-11ea-a13a-137349068a90.jpg   
3  2013-06-09 16:01:41.000  8e6994f4-21bc-11ea-a13a-137349068a90.jpg   
4  2013-06-09 16:01:42.000  948b29e2-21bc-11ea-a13a-137349068a90.jpg   

   seq_frame_num  seq_num_frames  sub_location  CC  \
0              0              10           NaN  BZ   
1              1              10           NaN  BZ   
2              2              10           NaN  BZ   
3              3              10           NaN  BZ   
4              4              10           NaN  BZ   

                                     filename  net_id idx  category_id  
0  8b31d3be-21bc-11ea-a13a-137349068a90_1.jpg   163.0   1        372.0  
1  8cf202be-21bc-11ea-a13a-137349068a90_1.jpg   163.0   1        372.0  
2  8a87e62e-21bc-11ea-a13a-137349068a90_1.jpg   163.0   1        372.0  
3  8e6994f4-21bc-11ea-a13a-137349068a90_1.jpg   163.0   1        372.0  
4  948b29e2-21bc-11ea-a13a-137349068a90_1.jpg   163.0   1        372.0

In [203]:
dirs = {
    "base" : "20210523", 
    "BZ" : "20210503BZ",
    "ZZ" : "20210503ZZ",
    "KE" : "20210503KE"
}
results = {}

In [205]:
for d in dirs:
    results[d] = resultstabletest(dirs[d], df_test_info_gps)
    #print(len(results[d]))
    #print(results[d][results[d].isnull().sum(axis=1) > 0])
    

all boxes 263504
testset 60190
#seq-test 11057
#img-test 60190
Dir 20210523
Read  20210523/topk_ids1621649028.191726.csv 33435
Read  20210523/topk_ids1621653075.488684.csv 33435
Read  20210523/topk_ids1621698904.931239.csv 33435
Read  20210523/topk_ids1621711402.173765.csv 33435
Read  20210523/topk_ids1621688001.166177.csv 33435
Read  20210523/topk_ids1621725310.266132.csv 33435
Read  20210523/topk_ids1621710168.691922.csv 33435
Read  20210523/topk_ids1621693804.599164.csv 33435
Read  20210523/topk_ids1621715449.980235.csv 33435
Read  20210523/topk_ids1621638454.126146.csv 33435
Read  20210523/topk_ids1621631935.8355.csv 33435
Read  20210523/topk_ids1621609898.519293.csv 33435
Read  20210523/topk_ids1621624175.617741.csv 33435
Read  20210523/topk_ids1621684306.933254.csv 33435
Read  20210523/topk_ids1621644271.961.csv 33435
Read  20210523/topk_ids1621699433.278051.csv 33435
Read  20210523/topk_ids1621707176.976596.csv 33435
Read  20210523/topk_ids1621705064.038477.csv 33435
Read  20210

Read  20210523/topk_ids1621655183.137594.csv 33435
Read  20210523/topk_ids1621695913.919159.csv 33435
Read  20210523/topk_ids1621710697.114814.csv 33435
Read  20210523/topk_ids1621709992.555019.csv 33435
Read  20210523/topk_ids1621679202.473085.csv 33435
Read  20210523/topk_ids1621648325.604701.csv 33435
Read  20210523/topk_ids1621689581.151651.csv 33435
Read  20210523/topk_ids1621642160.173602.csv 33435
Read  20210523/topk_ids1621692571.483324.csv 33435
Read  20210523/topk_ids1621679378.266407.csv 33435
Read  20210523/topk_ids1621680787.186755.csv 33435
Read  20210523/topk_ids1621645680.907324.csv 33435
Read  20210523/topk_ids1621688879.171981.csv 33435
Read  20210523/topk_ids1621693452.990574.csv 33435
Read  20210523/topk_ids1621705591.528555.csv 33435
Read  20210523/topk_ids1621697498.524475.csv 33435
Read  20210523/topk_ids1621612367.168214.csv 33435
Read  20210523/topk_ids1621609547.298069.csv 33435
Read  20210523/topk_ids1621673928.211525.csv 33435
Read  20210523/topk_ids16217092

Read  20210523/topk_ids1621658172.624196.csv 33435
Read  20210523/topk_ids1621724077.817782.csv 33435
Read  20210523/topk_ids1621659402.936382.csv 33435
Read  20210523/topk_ids1621706648.547632.csv 33435
Read  20210523/topk_ids1621616418.873237.csv 33435
Read  20210523/topk_ids1621701892.180195.csv 33435
Read  20210523/topk_ids1621678150.847322.csv 33435
Read  20210523/topk_ids1621652195.358597.csv 33435
Read  20210523/topk_ids1621644095.60297.csv 33435
Read  20210523/topk_ids1621622059.757177.csv 33435
Read  20210523/topk_ids1621686592.893068.csv 33435
Read  20210523/topk_ids1621621002.326169.csv 33435
Read  20210523/topk_ids1621655006.130934.csv 33435
Read  20210523/topk_ids1621674631.143769.csv 33435
Read  20210523/topk_ids1621721963.862044.csv 33435
Read  20210523/topk_ids1621704889.261103.csv 33435
Read  20210523/topk_ids1621722493.904005.csv 33435
Read  20210523/topk_ids1621638631.439933.csv 33435
Read  20210523/topk_ids1621700313.049288.csv 33435
Read  20210523/topk_ids162170735

Read  20210523/topk_ids1621641279.235347.csv 33435
Read  20210523/topk_ids1621698025.522937.csv 33435
Read  20210523/topk_ids1621641104.301802.csv 33435
Read  20210523/topk_ids1621699785.822906.csv 33435
Read  20210523/topk_ids1621704007.65221.csv 33435
Read  20210523/topk_ids1621689055.105399.csv 33435
Read  20210523/topk_ids1621625236.328651.csv 33435
Read  20210523/topk_ids1621640220.540132.csv 33435
Read  20210523/topk_ids1621685540.495425.csv 33435
Read  20210523/topk_ids1621652020.32559.csv 33435
Read  20210523/topk_ids1621726717.780759.csv 33435
Read  20210523/topk_ids1621694331.057244.csv 33435
Read  20210523/topk_ids1621719674.315414.csv 33435
Read  20210523/topk_ids1621629822.823528.csv 33435
Read  20210523/topk_ids1621699960.654026.csv 33435
Read  20210523/topk_ids1621623999.980057.csv 33435
Read  20210523/topk_ids1621717561.790001.csv 33435
Read  20210523/topk_ids1621631583.299213.csv 33435
Read  20210523/topk_ids1621723725.370018.csv 33435
Read  20210523/topk_ids1621706825

Read  20210503ZZ/topk_ids1620072926.389138.csv 33435
Read  20210503ZZ/topk_ids1620072221.011523.csv 33435
Read  20210503ZZ/topk_ids1620074861.360127.csv 33435
Read  20210503ZZ/topk_ids1620074158.709766.csv 33435
Read  20210503ZZ/topk_ids1620073453.55044.csv 33435
Read  20210503ZZ/topk_ids1620071868.739627.csv 33435
Read  20210503ZZ/topk_ids1620070106.747327.csv 33435
Read  20210503ZZ/topk_ids1620072750.384842.csv 33435
Read  20210503ZZ/topk_ids1620071340.017072.csv 33435
Read  20210503ZZ/topk_ids1620070987.391925.csv 33435
Read  20210503ZZ/topk_ids1620071163.567349.csv 33435
Read  20210503ZZ/topk_ids1620074509.498024.csv 33435
Read  20210503ZZ/topk_ids1620072397.558469.csv 33435
Read  20210503ZZ/topk_ids1620072573.464923.csv 33435
Read  20210503ZZ/topk_ids1620069931.650616.csv 33435
Read  20210503ZZ/topk_ids1620072044.888112.csv 33435
Read  20210503ZZ/topk_ids1620071692.502794.csv 33435
Read  20210503ZZ/topk_ids1620073982.231135.csv 33435
Read  20210503ZZ/topk_ids1620073102.031133.csv 

In [206]:
categories = {}
for d in ["EC","GT","RW","ZZ","KE","BR","BZ"]:
    categories[d] = sorted(list(pd.read_csv("train_split_" + d + "_md3_256_80.csv").category_id.value_counts().index))
    categories[d].extend(sorted(list(pd.read_csv("valid_split_" + d + "_md3_256_20.csv").category_id.value_counts().index)))
    categories[d] = set(categories[d])

In [763]:
CONF = 0.749
PMF_CONF = 0.0

# correct the predictions
def get_specialist(CC, filename):
    if CC in results:
        df = results[CC]
        return df[df.filename == filename].squeeze()
    return None
   
    
class Box:
    def __init__(self, box):
        self._box = box
        self._valid = True
        self._low_confidence = False
        self._overwrite = False
        self._confidence_bak = 0.0 # backup confidence when resetting
        self.check_confidence()
        if not self.check_valid():
            self.use_specialist()
            self.check_confidence()
            
    def area(self):
        # the area of the detected bounding box
        d = self.detection()
        return 0.0
    
    def category_id(self):
        return self._box.category_id
    
    def check_confidence(self):
        self._low_confidence = False
        if self._box.confidence < CONF:
            self._low_confidence = True
        
    def check_valid(self):
        valid_cats = categories[self._box.CC]

        self._valid = True
        if self._box.category_id not in valid_cats:
            # print("Invalid", self._box.category_id)
            self._valid = False
        return self._valid
    
    def confidence(self):
        return self._box.confidence
    
    def detection(self):
        idx = int(self._box.idx) - 1
        return self._box.detections[idx]
        
    def dump(self):
        print((self._box.category_id, self._box.confidence, self._box["name"]))
        
    def net_id(self):
        return self._box.net_id
    
    def score(self):
        # what is the best score
        # the area plus the confidence
        # the position in the image
        # is edge touching hurting ?
        return self._box.confidence
    
    def use_specialist(self, reset=True):
        other = get_specialist(self._box.CC, self._box.filename)
        if other is None:
            #print("Fatal: non existing country/filename",row.CC,row.filename)
            if reset:
                self._confidence_bak = self._box.confidence
                self._box.confidence = 0.0
        else:
            # use the specialist
            self._overwrite = True
            self._box.net_id = other.net_id
            self._box.confidence = other.confidence
            self._box.category_id = other.category_id
            
    def valid(self):
        return self._valid
    
    def wholeness(self):
        # return the number of edges touching the border
        # used for ranking
        return 1.0
    
class Frame:
    def __init__(self, frame):
        self._boxes = []
        for i,box in frame.iterrows():
            self._boxes.append(Box(box))

        self._image_id = frame.iloc[0].image_id
        idx = image_priors["image_id"] == self._image_id
        self._net_id, self._confidence = image_priors[idx][["net_id","confidence"]].squeeze()
        self._category_id = class_map(self._net_id)
        
    def count(self):
        
        pred = []
        for b in self.valid_boxes():
            pred.append(b.net_id())
        
        return pred
    
    def detections(self):
        return [b.detection() for b in self._boxes]
    
    def dropped(self):
        # function to tell if the frame has resetted boxes
        dropped = 0
        for b in self._boxes:
            if b._overwrite == False and b._box.confidence == 0.0:
                if b._confidence_bak > CONF: 
                    # check for a high confidence drop
                    # we want to still count that
                    dropped += 1
        return dropped
    
    def duplicates(self):
        # get the list of duplicate images
        empty = [b for b in self._boxes]
        pred = [b for b in self._boxes]
        # duplicates are images
        duplicates = (set(empty) & set(pred))
        # and re-add the found entry (high confidence)
        dc = 0
        for dup in duplicates:
            for e in empty[dup]:
                pred[dup].append(max(set(pred[dup]), key=pred[dup].count))
                dc += 1
            
    def dump(self):
        for b in self._boxes:
            b.dump()
    
    def rank(self):
        # rank the bounding boxes
        # use y position, and wholeness
        pass
    
    def score(self):
        # we calculate an error score based on delta boxes/detections
        # and on the number of species
        # IDEA: MST and the cost of change, how much does it cost
        # to change the category of a box
        
        # PERFECT SCORE FOR 1 FRAME
        # BOXES == DETECTION && NR_SPECIES == 1 && CONFIDENCE = BOXES
        nr_species = len(set(self.count()))
        nr_detections = len(self.detections())
        nr_boxes = len(self._boxes)
        total_confidence = sum([b.confidence for b in self._boxes])
        # we assume at best 1 species and all high confidence
        # boxes should have a decent prediction (empty is allowed)
        score = (nr_species - 1) ** 2 + (nr_detections - nr_boxes) ** 2
        score += (nr_boxes - total_confidence)
        ## we have to incorperate the mistake, penalty is high
        #score += nr_mistakes
        return score
    
    def summed_confidence(self, conf):
        sc = collections.Counter()
        for b in self._boxes:
            if b.confidence() > conf:
                sc[b.net_id()] += b.confidence()
        return sc
    
    def valid_boxes(self):
        return [b for b in self._boxes if not b._low_confidence]
            
class Sequence:
    def __init__(self, seq):
        self._seq = seq
        self._frames = []
        self._removed = 0
        for i, img in seq.groupby("image_id"):
            self._frames.append(Frame(img))
    
    def __repr__(self):
        return str(self._seq.seq_id.unique()[0])
    
    def __str__(self):
        return str(self._seq.seq_id.unique()[0])
    
    def avg_confidence(self):
        return self._seq["confidence"].mean()    
    
    def _count(self):
        counts = collections.defaultdict(list)
        dropped = 0
        for f in self._frames:
            frame_counts = f.count()
            # get the number of high confidence dropped boxes
            dropped += f.dropped()
            c = collections.Counter(frame_counts)
            for net_id, cnt in c.items():
                counts[net_id].append(cnt)

        if dropped > 0 and len(self._frames) > 1:
            # if we do have hight confidence dropped
            # and we work on a decent sequence
            # reset the scores ?!
            counts = collections.defaultdict(list)
        return counts
        
    def count(self):
        counts = self._count()
        
        counts = self.tie(counts)
        #counts = self.kudde(counts)
        counts = self.update(counts)
        return self.madmax(counts)

    def update(self, counts):
        if len(counts) <= 1:
            return counts
        
        pmf = self.prob_combined(counts)
        
        maxconf = 0
        maxid   = 0
        for key in pmf:
            if pmf[key] > maxconf:
                maxconf = pmf[key]
                maxid = key
                
        if maxconf > PMF_CONF:
            #rint(counts)
            #rint(pmf)
            for k in list(counts):
                if k == maxid:
                    continue
                del counts[k]
                self._removed += 1
            #rint(counts)
            
        return counts
        
    def kudde(self, counts):
        if len(counts) <= 1:
            return counts
        
        pmf_tc = self.prob_temporal_consistency(counts)
        categories = list(counts.keys())
        if len(categories) == 2:
            a = len(counts[categories[0]])
            b = len(counts[categories[1]])
            
            ids = pmf_tc.argleq(0.25)
            for d in ids:
                del counts[d]
            self._removed += len(ids)
       #     if a == 1 and b > 2:
       #         #print(str(self), counts, pmf_tc, self.summed_confidence(0.0))
       #         #self._removed += 1
       #         del counts[categories[0]]
       #         pass
       #     elif b == 1 and a > 2:
       #         #print(str(self), counts, pmf_tc, self.summed_confidence(0.0))
       #         del counts[categories[1]]
       #         #self._removed += 1
       ##         pass
       #     else:
       #         #if len(ids) > 0:
       #         #    print(str(self), counts, self.summed_confidence(0.0), pmf_tc)
       #         pass
        
        #if 24 in categories and 23 in categories:
        #    counts[23] = [x+y for x,y in zip_longest(counts[23], counts[24] , fillvalue=0)]
        #    for k in list(counts):
        #        if k == 23:
        #            continue
        #        del counts[k]
            
        #if 24 in categories and 25 in categories:
        #    counts[25] = [x+y for x,y in zip_longest(counts[25], counts[24] , fillvalue=0)]
        #    for k in list(counts):
        #        if k == 25:
        #            continue
        #        del counts[k]
            
        return counts
        
    def tie(self, counts):
        if len(counts) <= 1:
            return counts
        # check if the counts are a tie
        expected_value = sum(next(iter(counts.values()))) # check for an empty dictionary first if that's possible
        all_equal = all(sum(value) == expected_value for value in counts.values())
        if all_equal and expected_value == 1:
            #print("TIE", str(self._seq.seq_id), counts)
            maxprior = 10
            maxnetid = 0
            for k in counts:
                if k > 0:
                    if prior[k] < maxprior:
                        maxprior = prior[k]
                        maxnetid = k
                        
            for k in list(counts):
                if k == maxnetid:
                    continue
                del counts[k]
        return counts
            
    def detections(self):
        return [f.detections() for f in self._frames]
            
    def dump(self):
        for f in self._frames:
            print("- Frame  #boxes=", len(f.detections()))
            f.dump()
        #print(self.detections())
    
    def how_confused(self, conf=CONF):
        # this functions telss how confused the network
        # output for the bounding boxes is
        m = self.summed_confidence(conf)
        total_conf = 0
        if len(m) > 0:
            for k,v in m.items():
                total_conf += v
            first = sorted(m.items(), reverse=True, key=lambda item: item[1])[0][1]
        
            return 1.0 - first/total_conf
        return 0.0

    def hungarian(self):            

        delta_time = 1 # minute
        detections = self.detections()
        
        # create munkres matrix
        for frame in detections:
            pass
            #
    
    def madmax(self, counts):
        totalsum = 0
        for c in counts:
            res = counts[c]
            def mad(lst):
                s = sum(lst)
                l = float(len(lst))
                avg = s / l
                t = 0.
                for x in lst:
                    t += (x - avg)
                return t/l
        
            counts[c] = max(res) + mad(res)
            totalsum += counts[c]

        assert(totalsum <= self.nr_boxes())
        return counts

    def prob_box_confidences(self):
        pmf = PMF()
        for f in self._frames:
            fsc = f.summed_confidence(0.0)
            pmf += fsc
        pmf.normalize()
        return pmf
    
    def prob_combined(self, counts):
        tc = 0.45 * self.prob_temporal_consistency(counts)
        bc = 0.20 * self.prob_box_confidences()
        ic = 0.25 * self.prob_image_classification()
        oc = 0.10 * self.prob_old_classification()
        pmf = PMF(tc + bc + ic + oc)
        pmf.normalize()
        return pmf

    def prob_image_classification(self):
        pmf = PMF()
        for f in self._frames:
            pmf[int(f._net_id)] += 1
        pmf.normalize()
        return pmf
    
    def prob_old_classification(self):
        pmf = PMF()
        for f in self._frames:
            idx = old_results["image_id"] == f._image_id
            net_mode = old_results[idx][["net_id"]].mode()["net_id"]
            if len(net_mode):
                cat_mode = int(net_mode[0])
                pmf[cat_mode] += 1
        pmf.normalize()
        return pmf

    def prob_temporal_consistency(self, counts):
        pmf = PMF()
        for k, c in counts.items():
            pmf[k] += len(c)
        pmf.normalize()
        return pmf
    
    def score(self):
        # we calculate an error score
        nr_species = self.nr_species()
        # we assume at best 1 species and all high confidence
        # boxes should have a decent prediction (empty is allowed)
        score = (nr_species - 1.) ** 2. + (self.nr_detections() - self.nr_boxes()) ** 2. + (self.nr_boxes() - self.sum()) ** 2.
        # TODO: add penalty for confidences
        # TODO: maybe add penaly for high variance (when hungarian, check the deltatime)
        
        return score
        
    def nr_boxes(self):
        return len(self._seq)
    
    def nr_detections(self):
        # md3 count
        detections = self.detections()
        nr_detections = 0.
        for d in detections:
            nr_detections += len(d)
        return nr_detections
    
    def nr_frames(self):
        return len(self._frames)
    
    def nr_species(self):
        species_set = set(self.count())
        if 0 in species_set:
            species_set.remove(0) # remove empty prediction
        return len(species_set)
    
    def species(self):
        # guess species by max voting
        c = collections.Counter()
        for f in self._frames:
            c[int(f._net_id)] += 1
            #print(f._category_id, f._confidence)
        return c
    
    def species_old(self):
        c = collections.Counter()
        for f in self._frames:
            net_mode = old_results[old_results["image_id"] == f._image_id][["net_id"]].mode()["net_id"]
            cat_mode = int(net_mode[0])
            c[cat_mode] += 1
        return c

    def sum(self):
        count = self.count()
        return sum([count[c] for c in count])
         
    def summed_confidence(self, conf=CONF):
        sc = collections.Counter()
        for f in self._frames:
            fsc = f.summed_confidence(conf)
            sc += fsc
        return sc
    
    def visualize(self):
        visualize_sequence(self._seq, self._seq.seq_id, "test", thresh=CONF)

# nr of species should be 1
# nr of boxes

# create a group aggregator
groups = results["base"].groupby("seq_id")
seq_counts = collections.defaultdict(list)
total = 0
scorepile = {}
for seq_id, seq in tqdm.tqdm(groups):
    s = Sequence(seq)
    s.how_confused()
    scorepile[str(s)] = s
    seq_counts[seq_id] = s.count()
    # count the total number of animals as a reference check
    total += sum([seq_counts[seq_id][b] for b in seq_counts[seq_id]])
print(total)

100%|██████████| 5456/5456 [01:06<00:00, 81.58it/s] 

5177.0


In [765]:
count = sum([v._removed for k,v in scorepile.items()])
print(count)

100


In [766]:
# Analyze the scorepile
scorepile = {k: v for k, v in sorted(scorepile.items(), key=lambda item: item[1].score(), reverse=True)}
print("="*5,"scorepile","="*5)
res = list(scorepile.keys())
for i, seq_id in enumerate(res[:5]):
    print("#" + str(i), seq_id, scorepile[seq_id].score())
#print(scorepile)
#print(scorepile)
#print(first)
  
     
#for k,v in scorepile.items():
#    sc = v.summed_confidence()
#    if next(iter(sc.keys())) == 71:
#        print(k)
#        print(v.summed_confidence())
#        print(v.nr_species(), v.count())
#        #v.visualize()
#        break
##scorepile["a91738a8-0cd3-11eb-bed1-0242ac1c0002"].visualize()
#scorepile["a9173ae2-0cd3-11eb-bed1-0242ac1c0002"].visualize()

    


def tst(seq, counts):
    self = seq
    pmf_tc = prob_box_confidences(seq)
    categories = list(counts.keys())
    if len(categories) == 2:
        a = len(counts[categories[0]])
        b = len(counts[categories[1]])
        print("pim=",pmf_tc)
        

        
def analyze(seq_id):
    seq = scorepile[seq_id]
    scorepile[seq_id].visualize()
 
    print("** Confusion scores **")
    print(scorepile[seq_id].how_confused())
    print("** Confidence summed **")
    #print(scorepile[seq_id].summed_confidence())
    #print(scorepile[seq_id].summed_confidence(0.0))
    scorepile[seq_id].dump()
    
    #print("** full image predictions **")
    #for f in seq._frames:
    #    print(f._category_id, f._confidence)
    print("prob_temporal_consistency")
    print(seq.prob_temporal_consistency(seq._count()))
    print("prob_box_confidences")
    print(seq.prob_box_confidences())
    print("prob_image_classification")
    print(seq.prob_image_classification())
    print("prob_old_classification")
    print(seq.prob_old_classification())
    print(prob_combined(seq, seq._count()))
    print("** madmax result **")
    for k,v in seq.count().items():
        print(class_map(k),":", v)
        
    #tst(seq, seq._count())
analyze(res[0])
#analyze("a91a52e0-0cd3-11eb-bed1-0242ac1c0002")
#first.visualize()
#first.dump()
# how many sequences are there with 1 frame 1 box
cc = collections.Counter()
for seq_id, seq in scorepile.items():
    cc[seq.nr_species()] += 1
#print(cc)
# how many sequences are there with 1 frame x box

===== scorepile =====
#0 a91738a8-0cd3-11eb-bed1-0242ac1c0002 7744.0
#1 a9173ae2-0cd3-11eb-bed1-0242ac1c0002 7056.0
#2 a917398e-0cd3-11eb-bed1-0242ac1c0002 5929.0
#3 a9173a42-0cd3-11eb-bed1-0242ac1c0002 5476.0
#4 a917daf6-0cd3-11eb-bed1-0242ac1c0002 5184.0
** Confusion scores **
0.299593878949561
** Confidence summed **
- Frame  #boxes= 8
(71, 0.7520046630438338, 'bos taurus')
(71, 0.6569311258352902, 'bos taurus')
(71, 0.6443867815351714, 'bos taurus')
(71, 0.841486958235922, 'bos taurus')
(71, 0.6636518722652358, 'bos taurus')
(71, 0.6336484731585267, 'bos taurus')
(70, 0.4546757790345501, 'capra aegagrus')
(70, 0.7167945449915938, 'capra aegagrus')
- Frame  #boxes= 11
(71, 0.7469303324620683, 'bos taurus')
(71, 0.5596176644776787, 'bos taurus')
(71, 0.5979018836109726, 'bos taurus')
(71, 0.7666367961186312, 'bos taurus')
(71, 0.6328965646557903, 'bos taurus')
(71, 0.6857366757429376, 'bos taurus')
(71, 0.4358122192396976, 'bos taurus')
(96, 0.6474486361440106, 'aepyceros melampus')


In [ ]:
# original : Counter({1: 4202, 0: 1133, 2: 115, 3: 5, 4: 1})
# after tie: Counter({1: 4225, 0: 1136, 2: 91, 3: 3, 4: 1})
# kudde      Counter({1: 4273, 0: 1136, 2: 43, 3: 3, 4: 1})
# kudde - 0  Counter({1: 4119, 0: 1294, 2: 39, 3: 3, 4: 1})


In [ ]:
# 1st submit 5898.0 
# 2nd submit 5309 # hopla high score
# 3rd submit 5314 # worse !!
# 4rd submit 5306 # high score, this is so weird
# 5th submit 5278.0 # break ties, conservative
# maybe submit 5263.0 # cows
# superhack: 5224 (drop insignificant doubles, dump cows)
# clean hack 5226 (drop loose ends)
# cleanast solution PMF 0.6
# cleanast solution 5177 PMF 0.4
# cleanast solution 5177 PMF 0.0

In [768]:
output = []
for seq_id in seq_counts:
    c = collections.Counter(seq_counts[seq_id])
    res = []
    cnts = [0 for i in range(205)]
    for category, cnt in c.items():
        cnts[category] = cnt
    res += [seq_id] + cnts[1:]
    output.append(res)
    
sub_tmp = pd.read_csv("sample_submission.csv")
sub_tmp = sub_tmp.set_index(["Id"])

col_Predicted = [col for col in sub_tmp.columns if "Predicted" in col]
sub_tmp[col_Predicted] = 0

new_tmp = pd.DataFrame(output, columns=["Id", *sub_tmp.columns])
new_tmp = new_tmp.set_index(["Id"])
sub_tmp.loc[new_tmp.index] = np.nan
sub_tmp = sub_tmp.combine_first(new_tmp)

print(sub_tmp.sum(axis=1).sum())
sub_tmp.to_csv("subtmp.csv", index=True)


5007.0


In [745]:
sub_tmp.head()

Predicted2  Predicted3  Predicted4  \
Id                                                                         
2966a68a-6fe2-11eb-844f-0242ac1c0002         0.0         0.0         0.0   
296781a4-6fe2-11eb-844f-0242ac1c0002         0.0         0.0         0.0   
2967a1fc-6fe2-11eb-844f-0242ac1c0002         0.0         0.0         0.0   
2967bdd6-6fe2-11eb-844f-0242ac1c0002         0.0         0.0         0.0   
29681182-6fe2-11eb-844f-0242ac1c0002         0.0         0.0         0.0   

                                      Predicted6  Predicted7  Predicted8  \
Id                                                                         
2966a68a-6fe2-11eb-844f-0242ac1c0002         0.0         0.0         0.0   
296781a4-6fe2-11eb-844f-0242ac1c0002         0.0         0.0         0.0   
2967a1fc-6fe2-11eb-844f-0242ac1c0002         0.0         0.0         0.0   
2967bdd6-6fe2-11eb-844f-0242ac1c0002         0.0         0.0         0.0   
29681182-6fe2-11eb-844f-0242ac1c0002         0.0         0.0         0.0   

                                      Predicted9  Predicted10  Predicted12  \
Id                                                                           
2966a68a-6fe2-11eb-844f-0242ac1c0002         0.0          0.0          0.0   
296781a4-6fe2-11eb-844f-0242ac1c0002         0.0          0.0          0.0   
2967a1fc-6fe2-11eb-844f-0242ac1c0002         0.0          0.0          0.0   
2967bdd6-6fe2-11eb-844f-0242ac1c0002         0.0          0.0          0.0   
29681182-6fe2-11eb-844f-0242ac1c0002         0.0          0.0          0.0   

                                      Predicted13  ...  Predicted559  \
Id                                                 ...                 
2966a68a-6fe2-11eb-844f-0242ac1c0002          0.0  ...           0.0   
296781a4-6fe2-11eb-844f-0242ac1c0002          0.0  ...           0.0   
2967a1fc-6fe2-11eb-844f-0242ac1c0002          0.0  ...           0.0   
2967bdd6-6fe2-11eb-844f-0242ac1c0002          0.0  ...           0.0   
29681182-6fe2-11eb-844f-0242ac1c0002          0.0  ...           0.0   

                                      Predicted562  Predicted563  \
Id                                                                 
2966a68a-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
296781a4-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
2967a1fc-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
2967bdd6-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
29681182-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   

                                      Predicted564  Predicted565  \
Id                                                                 
2966a68a-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
296781a4-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
2967a1fc-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
2967bdd6-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
29681182-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   

                                      Predicted566  Predicted567  \
Id                                                                 
2966a68a-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
296781a4-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
2967a1fc-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
2967bdd6-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   
29681182-6fe2-11eb-844f-0242ac1c0002           0.0           0.0   

                                      Predicted568  Predicted570  Predicted571  
Id                                                                              
2966a68a-6fe2-11eb-844f-0242ac1c0002           0.0           0.0           0.0  
296781a4-6fe2-11eb-844f-0242ac1c0002           0.0           0.0           0.0  
2967a1fc-6fe2-11eb-844f-0242ac1c0002           0.0           0.0           0.0  
2967bdd6-6fe2-11eb-844f-0242ac1c0002           0.0           0.0           0.0  
296

In [746]:
sub_tmp.describe()

Predicted2    Predicted3    Predicted4    Predicted6  Predicted7  \
count  11057.000000  11057.000000  11057.000000  11057.000000     11057.0   
mean       0.003708      0.009948      0.000904      0.008954         0.0   
std        0.114461      0.101946      0.030061      0.099798         0.0   
min        0.000000      0.000000      0.000000      0.000000         0.0   
25%        0.000000      0.000000      0.000000      0.000000         0.0   
50%        0.000000      0.000000      0.000000      0.000000         0.0   
75%        0.000000      0.000000      0.000000      0.000000         0.0   
max        6.000000      2.000000      1.000000      3.000000         0.0   

         Predicted8    Predicted9   Predicted10  Predicted12  Predicted13  \
count  11057.000000  11057.000000  11057.000000      11057.0      11057.0   
mean       0.007959      0.000452      0.032106          0.0          0.0   
std        0.110624      0.021261      0.178331          0.0          0.0   
min        0.000000      0.000000      0.000000          0.0          0.0   
25%        0.000000      0.000000      0.000000          0.0          0.0   
50%        0.000000      0.000000      0.000000          0.0          0.0   
75%        0.000000      0.000000      0.000000          0.0          0.0   
max        3.000000      1.000000      2.000000          0.0          0.0   

       ...  Predicted559  Predicted562  Predicted563  Predicted564  \
count  ...  11057.000000       11057.0       11057.0       11057.0   
mean   ...      0.000362           0.0           0.0           0.0   
std    ...      0.023293           0.0           0.0           0.0   
min    ...      0.000000           0.0           0.0           0.0   
25%    ...      0.000000           0.0           0.0           0.0   
50%    ...      0.000000           0.0           0.0           0.0   
75%    ...      0.000000           0.0           0.0           0.0   
max    ...      2.000000           0.0           0.0           0.0   

       Predicted565  Predicted566  Predicted567  Predicted568  Predicted570  \
count   11057.00000   11057.00000       11057.0  11057.000000       11057.0   
mean        0.00009       0.00009           0.0      0.000633           0.0   
std         0.00951       0.00951           0.0      0.025154           0.0   
min         0.00000       0.00000           0.0      0.000000           0.0   
25%         0.00000       0.00000           0.0      0.000000           0.0   
50%         0.00000       0.00000           0.0      0.000000           0.0   
75%         0.00000       0.00000           0.0      0.000000           0.0   
max         1.00000       1.00000           0.0      1.000000           0.0   

       Predicted571  
count       11057.0  
mean            0.0  
std             0.0  
min             0.0  
25%             0.0  
50%             0.0  
75%             0.0  
max             0.0  

[8 rows x 204 columns]

In [769]:
sub_tmp[col_Predicted].sum(axis=0).sum()

5007.0

In [748]:
hard_ones = [257, 130, 133, 402, 406, 407, 408, 412, 415, 417, 420, 296, 306, 571, 322, 323, 330, 77, 333, 80, 339, 342, 92, 349, 355, 356, 229, 114, 119, 250, 251, 252, 253]


In [749]:
hard_ones = sorted(hard_ones)

In [750]:
hard_ids = ["Predicted" + str(h) for h in hard_ones]
#class_map.name(hard_ones[0])

In [751]:
sub_tmp[hard_ids].sum(axis=0).sum()

0.0